In [ ]:
!kaggle datasets download -d yasserh/breast-cancer-dataset

In [ ]:
!unzip -o breast-cancer-dataset.zip

In [109]:
import numpy as np
import torch
from torch import nn
from torch.autograd import Variable
from sklearn.datasets import load_iris
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import LabelEncoder
from tensorflow.keras.utils import to_categorical
import torch.nn.functional as F
import pandas as pd

In [110]:
class Model(nn.Module):
    def __init__(self, input_dim):
        super(Model, self).__init__()
        self.layer1 = nn.Linear(input_dim,50)
        self.layer2 = nn.Linear(50, 20)
        self.layer3 = nn.Linear(20, 3)
        
    def forward(self, x):
        x = F.relu(self.layer1(x))
        x = F.relu(self.layer2(x))
        x = F.softmax(self.layer3(x)) # To check with the loss function
        return x

In [111]:
class_names = ['Malignant', 'Benign']
data = pd.read_csv('breast-cancer.csv', index_col=0)
data[1:10]

diagnosis  radius_mean  texture_mean  perimeter_mean  area_mean  \
id                                                                         
842517           M        20.57         17.77          132.90     1326.0   
84300903         M        19.69         21.25          130.00     1203.0   
84348301         M        11.42         20.38           77.58      386.1   
84358402         M        20.29         14.34          135.10     1297.0   
843786           M        12.45         15.70           82.57      477.1   
844359           M        18.25         19.98          119.60     1040.0   
84458202         M        13.71         20.83           90.20      577.9   
844981           M        13.00         21.82           87.50      519.8   
84501001         M        12.46         24.04           83.97      475.9   

          smoothness_mean  compactness_mean  concavity_mean  \
id                                                            
842517            0.08474           0.07864         0.08690   
84300903          0.10960           0.15990         0.19740   
84348301          0.14250           0.28390         0.24140   
84358402          0.10030           0.13280         0.19800   
843786            0.12780           0.17000         0.15780   
844359            0.09463           0.10900         0.11270   
84458202          0.11890           0.16450         0.09366   
844981            0.12730           0.19320         0.18590   
84501001          0.11860           0.23960         0.22730   

          concave points_mean  symmetry_mean           ...             \
id                                                     ...              
842517                0.07017         0.1812           ...              
84300903              0.12790         0.2069           ...              
84348301              0.10520         0.2597           ...              
84358402              0.10430         0.1809           ...              
843786                0.08089         0.2087           ...              
844359                0.07400         0.1794           ...              
84458202              0.05985         0.2196           ...              
844981                0.09353         0.2350           ...              
84501001              0.08543         0.2030           ...              

          radius_worst  texture_worst  perimeter_worst  area_worst  \
id                                                                   
842517           24.99          23.41           158.80      1956.0   
84300903         23.57          25.53           152.50      1709.0   
84348301         14.91          26.50            98.87       567.7   
84358402         22.54          16.67           152.20      1575.0   
843786           15.47          23.75           103.40       741.6   
844359           22.88          27.66           153.20      1606.0   
84458202         17.06          28.14           110.60       897.0   
844981           15.49          30.73           106.20       739.3   
84501001         15.09          40.68            97.65       711.4   

          smoothness_worst  compactness_worst  concavity_worst  \
id                                                               
842517              0.1238             0.1866           0.2416   
84300903            0.1444             0.4245           0.4504   
84348301            0.2098             0.8663           0.6869   
84358402            0.1374             0.2050           0.4000   
843786              0.1791             0.5249           0.5355   
844359              0.1442             0.2576           0.3784   
84458202            0.1654             0.3682           0.2678   
844981              0.1703             0.5401           0.5390   
84501001            0.1853             1.0580           1.1050   

          concave points_worst  symmetry_worst  fractal_dimension_worst  
id                                                                       
842517                  0.18

In [112]:
lb = LabelEncoder()
data['diagnosis'] = lb.fit_transform(data['diagnosis'])
features = data.iloc[:, 1:32].values
labels = np.array(data['diagnosis'])

In [113]:
features[1:10]

array([[2.057e+01, 1.777e+01, 1.329e+02, 1.326e+03, 8.474e-02, 7.864e-02,
        8.690e-02, 7.017e-02, 1.812e-01, 5.667e-02, 5.435e-01, 7.339e-01,
        3.398e+00, 7.408e+01, 5.225e-03, 1.308e-02, 1.860e-02, 1.340e-02,
        1.389e-02, 3.532e-03, 2.499e+01, 2.341e+01, 1.588e+02, 1.956e+03,
        1.238e-01, 1.866e-01, 2.416e-01, 1.860e-01, 2.750e-01, 8.902e-02],
       [1.969e+01, 2.125e+01, 1.300e+02, 1.203e+03, 1.096e-01, 1.599e-01,
        1.974e-01, 1.279e-01, 2.069e-01, 5.999e-02, 7.456e-01, 7.869e-01,
        4.585e+00, 9.403e+01, 6.150e-03, 4.006e-02, 3.832e-02, 2.058e-02,
        2.250e-02, 4.571e-03, 2.357e+01, 2.553e+01, 1.525e+02, 1.709e+03,
        1.444e-01, 4.245e-01, 4.504e-01, 2.430e-01, 3.613e-01, 8.758e-02],
       [1.142e+01, 2.038e+01, 7.758e+01, 3.861e+02, 1.425e-01, 2.839e-01,
        2.414e-01, 1.052e-01, 2.597e-01, 9.744e-02, 4.956e-01, 1.156e+00,
        3.445e+00, 2.723e+01, 9.110e-03, 7.458e-02, 5.661e-02, 1.867e-02,
        5.963e-02, 9.208e-03, 1.491e

In [114]:
labels[1:10]

array([1, 1, 1, 1, 1, 1, 1, 1, 1])

In [115]:
features_train, features_test, labels_train, labels_test = train_test_split(features, labels, random_state=42, shuffle=True)

In [116]:
# Training
model = Model(features_train.shape[1])
optimizer = torch.optim.Adam(model.parameters(), lr=0.01)
loss_fn = nn.CrossEntropyLoss()
epochs = 100

def print_(loss):
    print ("The loss calculated: ", loss)

In [117]:
# Not using dataloader
x_train, y_train = Variable(torch.from_numpy(features_train)).float(), Variable(torch.from_numpy(labels_train)).long()
for epoch in range(1, epochs+1):
    print ("Epoch #",epoch)
    y_pred = model(x_train)
    loss = loss_fn(y_pred, y_train)
    print_(loss.item())
    
    # Zero gradients
    optimizer.zero_grad()
    loss.backward() # Gradients
    optimizer.step() # Update

Epoch # 1
The loss calculated:  0.922476053237915
Epoch # 2
The loss calculated:  0.9223369359970093
Epoch # 3
The loss calculated:  0.9223369359970093
Epoch # 4
The loss calculated:  0.9223369359970093
Epoch # 5
The loss calculated:  0.9223369359970093
Epoch # 6
The loss calculated:  0.9223369359970093
Epoch # 7
The loss calculated:  0.9223369359970093
Epoch # 8
The loss calculated:  0.9223369359970093
Epoch # 9
The loss calculated:  0.9223369359970093
Epoch # 10
The loss calculated:  0.9223369359970093
Epoch # 11
The loss calculated:  0.9223369359970093
Epoch # 12
The loss calculated:  0.9223369359970093
Epoch # 13
The loss calculated:  0.9223369359970093
Epoch # 14
The loss calculated:  0.9223369359970093
Epoch # 15
The loss calculated:  0.9223369359970093
Epoch # 16
The loss calculated:  0.9223369359970093
Epoch # 17
The loss calculated:  0.9223369359970093
Epoch # 18
The loss calculated:  0.9223369359970093
Epoch # 19
The loss calculated:  0.9223369359970093
Epoch # 20
The loss ca

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  # This is added back by InteractiveShellApp.init_path()


In [118]:
# Prediction
x_test = Variable(torch.from_numpy(features_test)).float()
pred = model(x_test)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  # This is added back by InteractiveShellApp.init_path()


In [119]:
pred = pred.detach().numpy()
pred[1:10]

array([[1., 0., 0.],
       [1., 0., 0.],
       [1., 0., 0.],
       [1., 0., 0.],
       [1., 0., 0.],
       [1., 0., 0.],
       [1., 0., 0.],
       [1., 0., 0.],
       [1., 0., 0.]], dtype=float32)

In [120]:
print ("The accuracy is", accuracy_score(labels_test, np.argmax(pred, axis=1)))

The accuracy is 0.6223776223776224


In [121]:
labels_test[0]

0

In [122]:
torch.save(model, "travel_insurance-pytorch.pkl")

In [123]:
saved_model = torch.load("travel_insurance-pytorch.pkl")

In [124]:
np.argmax(saved_model(x_test[0]).detach().numpy(), axis=0)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:11: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  # This is added back by InteractiveShellApp.init_path()


0